# packages

In [52]:
import vectorbt as vbt
import numpy as np
import pandas as pd
from alpaca.trading.client import TradingClient
from alpaca.trading.requests import GetAssetsRequest
from alpaca.trading.enums import AssetClass, AssetStatus
from alpaca.data.historical import CryptoHistoricalDataClient, StockHistoricalDataClient
from alpaca.data.requests import CryptoBarsRequest
from alpaca.data.timeframe import TimeFrame
import plotly.graph_objs as go
from plotly.subplots import make_subplots
from datetime import datetime
import yaml
import yfinance as yf

# get list of stock and crypto symbols

In [53]:
keys = yaml.safe_load(open('..\keys.yaml', 'r'))

In [54]:
trading_client = TradingClient(keys['paper_key'], keys['paper_secret'])

In [55]:
search_params = GetAssetsRequest(asset_class = AssetClass.CRYPTO, status = AssetStatus.ACTIVE)
crypto_assets = trading_client.get_all_assets(search_params)
len(crypto_assets), crypto_assets[0]

(56,
 {   'asset_class': <AssetClass.CRYPTO: 'crypto'>,
     'attributes': [],
     'easy_to_borrow': False,
     'exchange': <AssetExchange.CRYPTO: 'CRYPTO'>,
     'fractionable': True,
     'id': UUID('f0a05db3-5c93-4524-8a32-2f2b8d4f12fc'),
     'maintenance_margin_requirement': 100.0,
     'marginable': False,
     'min_order_size': 0.003763643,
     'min_trade_increment': 1e-09,
     'name': 'Bitcoin Cash / US Dollar',
     'price_increment': 0.025,
     'shortable': False,
     'status': <AssetStatus.ACTIVE: 'active'>,
     'symbol': 'BCH/USD',
     'tradable': True})

In [56]:
df_crypto_assets = pd.DataFrame([dict(asset) for asset in crypto_assets])
df_crypto_assets.head()

id        asset_class  \
0  f0a05db3-5c93-4524-8a32-2f2b8d4f12fc  AssetClass.CRYPTO   
1  9a3baaff-11b0-4428-a63c-f6e3340694e1  AssetClass.CRYPTO   
2  0425de77-90d3-4ac9-b914-73423b4e42b8  AssetClass.CRYPTO   
3  3e242d92-02c9-42d8-a2a1-e04f8b2f8860  AssetClass.CRYPTO   
4  b1365689-2b1b-4b84-a263-67d5c622728d  AssetClass.CRYPTO   

               exchange    symbol                      name  \
0  AssetExchange.CRYPTO   BCH/USD  Bitcoin Cash / US Dollar   
1  AssetExchange.CRYPTO  BCH/USDC   Bitcoin Cash / USD Coin   
2  AssetExchange.CRYPTO   CRV/USD         Curve / US Dollar   
3  AssetExchange.CRYPTO   GRT/USD     The Graph / US Dollar   
4  AssetExchange.CRYPTO  GRT/USDC      The Graph / USD Coin   

               status  tradable  marginable  shortable  easy_to_borrow  \
0  AssetStatus.ACTIVE      True       False      False           False   
1  AssetStatus.ACTIVE      True       False      False           False   
2  AssetStatus.ACTIVE      True       False      False           False   
3  AssetStatus.ACTIVE      True       False      False           False   
4  AssetStatus.ACTIVE      True       False      False           False   

   fractionable  min_order_size  min_trade_increment  price_increment  \
0          True        0.003764         1.000000e-09          0.02500   
1          True        0.003738         1.000000e-09              NaN   
2          True        1.570537         1.000000e-09              NaN   
3          True        4.574356         1.000000e-09          0.00005   
4          True        4.629630         1.000000e-09              NaN   

   maintenance_margin_requirement attributes  
0                           100.0         []  
1                           100.0         []  
2                           100.0         []  
3                           100.0         []  
4                           100.0         []

In [57]:
df_crypto_assets.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 56 entries, 0 to 55
Data columns (total 16 columns):
 #   Column                          Non-Null Count  Dtype  
---  ------                          --------------  -----  
 0   id                              56 non-null     object 
 1   asset_class                     56 non-null     object 
 2   exchange                        56 non-null     object 
 3   symbol                          56 non-null     object 
 4   name                            56 non-null     object 
 5   status                          56 non-null     object 
 6   tradable                        56 non-null     bool   
 7   marginable                      56 non-null     bool   
 8   shortable                       56 non-null     bool   
 9   easy_to_borrow                  56 non-null     bool   
 10  fractionable                    56 non-null     bool   
 11  min_order_size                  56 non-null     float64
 12  min_trade_increment             56 non

# get list of active stocks

In [58]:
search_params = GetAssetsRequest(asset_class = AssetClass.US_EQUITY,status=AssetStatus.ACTIVE)
stock_assets = trading_client.get_all_assets(search_params)
len(stock_assets), stock_assets[0]

(11059,
 {   'asset_class': <AssetClass.US_EQUITY: 'us_equity'>,
     'attributes': [],
     'easy_to_borrow': False,
     'exchange': <AssetExchange.NASDAQ: 'NASDAQ'>,
     'fractionable': False,
     'id': UUID('4d4e6d5d-8f9c-44a8-9a64-b14443c2422d'),
     'maintenance_margin_requirement': 100.0,
     'marginable': False,
     'min_order_size': None,
     'min_trade_increment': None,
     'name': 'MicroCloud Hologram Inc. Ordinary Shares',
     'price_increment': None,
     'shortable': False,
     'status': <AssetStatus.ACTIVE: 'active'>,
     'symbol': 'HOLO',
     'tradable': False})

In [59]:
df_stock_assets = pd.DataFrame([dict(asset) for asset in stock_assets])
df_stock_assets.head()

id           asset_class  \
0  4d4e6d5d-8f9c-44a8-9a64-b14443c2422d  AssetClass.US_EQUITY   
1  92cea273-376f-4f79-a38e-059dedde9d80  AssetClass.US_EQUITY   
2  40cd693a-74da-4f0e-a8f5-bc5b172b1677  AssetClass.US_EQUITY   
3  2cdcf87d-8dd7-43d4-b56d-a2eb957ffafc  AssetClass.US_EQUITY   
4  dc476206-ff46-48d4-8436-45366d9be982  AssetClass.US_EQUITY   

               exchange symbol  \
0  AssetExchange.NASDAQ   HOLO   
1     AssetExchange.OTC  LCINQ   
2     AssetExchange.OTC   IMPM   
3     AssetExchange.OTC  QTTOY   
4     AssetExchange.OTC  IMPLQ   

                                                name              status  \
0           MicroCloud Hologram Inc. Ordinary Shares  AssetStatus.ACTIVE   
1                                LANNETT INC COM NEW  AssetStatus.ACTIVE   
2                        IMPAC MTG HLDGS INC COM NEW  AssetStatus.ACTIVE   
3  QUTOUTIAO INC American Depositary Shares - Spo...  AssetStatus.ACTIVE   
4                      IMPEL PHARMACEUTICALS INC COM  AssetStatus.ACTIVE   

   tradable  marginable  shortable  easy_to_borrow  fractionable  \
0     False       False      False           False         False   
1     False       False      False           False         False   
2     False       False      False           False         False   
3     False       False      False           False         False   
4     False       False      False           False         False   

  min_order_size min_trade_increment price_increment  \
0           None                None            None   
1           None                None            None   
2           None                None            None   
3           None                None            None   
4           None                None            None   

   maintenance_margin_requirement attributes  
0                           100.0         []  
1                           100.0         []  
2                           100.0         []  
3                           100.0         []  
4                           100.0         []

In [60]:
df_stock_assets.tradable.value_counts()

tradable
True     10726
False      333
Name: count, dtype: int64

# get btc/usd data from yfinance

In [107]:
# Download BTC/USD data
btc_data_yf = yf.download("BTC-USD", start="2010-01-01", end="2024-01-01")

# Display the data
btc_data_yf.head()

[*********************100%%**********************]  1 of 1 completed


Open        High         Low       Close   Adj Close  \
Date                                                                     
2014-09-17  465.864014  468.174011  452.421997  457.334015  457.334015   
2014-09-18  456.859985  456.859985  413.104004  424.440002  424.440002   
2014-09-19  424.102997  427.834991  384.532013  394.795990  394.795990   
2014-09-20  394.673004  423.295990  389.882996  408.903992  408.903992   
2014-09-21  408.084991  412.425995  393.181000  398.821014  398.821014   

              Volume  
Date                  
2014-09-17  21056800  
2014-09-18  34483200  
2014-09-19  37919700  
2014-09-20  36863600  
2014-09-21  26580100

# get data - all cryptos

In [62]:
client = CryptoHistoricalDataClient()

# Creating request object
request_params = CryptoBarsRequest(
                        symbol_or_symbols=df_crypto_assets['symbol'].tolist(),
                        timeframe=TimeFrame.Day,
                        start=datetime(2000, 1, 1),
                        end=datetime.now()
                        )

In [63]:
# btc_bars = client.get_crypto_bars(request_params)

# # Convert to dataframe
# df_crypto = btc_bars.df
# df_crypto

In [64]:
#df_crypto.to_pickle('..\\data\\df_crypto_daily.pickle')

In [65]:
df_crypto = pd.read_pickle('..\\data\\df_crypto_daily.pickle')

# df_crypto audit

In [66]:
df_crypto.info()

<class 'pandas.core.frame.DataFrame'>
MultiIndex: 35181 entries, ('AAVE/USDC', Timestamp('2023-08-18 05:00:00+0000', tz='UTC')) to ('YFI/USD', Timestamp('2024-01-01 06:00:00+0000', tz='UTC'))
Data columns (total 7 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   open         35181 non-null  float64
 1   high         35181 non-null  float64
 2   low          35181 non-null  float64
 3   close        35181 non-null  float64
 4   volume       35181 non-null  float64
 5   trade_count  35181 non-null  float64
 6   vwap         35181 non-null  float64
dtypes: float64(7)
memory usage: 2.0+ MB


In [67]:
df_crypto.index.get_level_values('symbol').unique()

Index(['AAVE/USDC', 'AAVE/USDT', 'AAVE/USD', 'AVAX/USDC', 'AVAX/USDT',
       'AVAX/USD', 'BAT/USDC', 'BAT/USD', 'BCH/BTC', 'BCH/USDC', 'BCH/USDT',
       'BCH/USD', 'BTC/USDC', 'BTC/USDT', 'BTC/USD', 'DOGE/USDC', 'DOGE/USDT',
       'CRV/USDC', 'CRV/USD', 'DOGE/USD', 'DOT/USDC', 'DOT/USD', 'ETH/BTC',
       'ETH/USDC', 'ETH/USDT', 'ETH/USD', 'GRT/USDC', 'GRT/USD', 'LINK/BTC',
       'LINK/USDC', 'LINK/USD', 'LINK/USDT', 'LTC/BTC', 'LTC/USDC', 'LTC/USDT',
       'LTC/USD', 'MKR/USDC', 'MKR/USD', 'SHIB/USDT', 'SHIB/USDC',
       'SUSHI/USDC', 'SUSHI/USDT', 'SHIB/USD', 'SUSHI/USD', 'UNI/BTC',
       'UNI/USDC', 'UNI/USDT', 'UNI/USD', 'USDC/USD', 'USDT/USDC', 'USDT/USD',
       'XTZ/USDC', 'XTZ/USD', 'YFI/USDC', 'YFI/USDT', 'YFI/USD'],
      dtype='object', name='symbol')

In [68]:
df_crypto.index.get_level_values('timestamp').min()

Timestamp('2021-01-01 06:00:00+0000', tz='UTC')

In [69]:
df_crypto.loc[('BTC/USD')]

open       high         low      close  \
timestamp                                                                
2021-01-01 06:00:00+00:00  29255.710  29682.290  28707.5600  29676.790   
2021-01-02 06:00:00+00:00  29678.340  34200.000  29555.9900  33769.520   
2021-01-03 06:00:00+00:00  33769.520  34812.930  32300.6100  32908.020   
2021-01-04 06:00:00+00:00  32907.360  33496.030  27900.0000  30441.570   
2021-01-05 06:00:00+00:00  30461.840  35851.420  29927.5500  35063.000   
...                              ...        ...         ...        ...   
2023-12-28 06:00:00+00:00  43219.050  43219.050  42168.3170  42703.000   
2023-12-29 06:00:00+00:00  42677.465  43111.110  41552.0500  42077.970   
2023-12-30 06:00:00+00:00  42105.110  42585.069  41536.2170  42206.355   
2023-12-31 06:00:00+00:00  42177.102  42852.700  42103.7605  42225.540   
2024-01-01 06:00:00+00:00  42212.570  43857.800  42212.5700  43412.165   

                                volume  trade_count          vwap  
timestamp                                                          
2021-01-01 06:00:00+00:00   848.874030      29639.0  29316.444625  
2021-01-02 06:00:00+00:00  2144.592516      60152.0  31941.412694  
2021-01-03 06:00:00+00:00  1838.695433      58725.0  33505.269474  
2021-01-04 06:00:00+00:00  2711.189503      69226.0  31267.965121  
2021-01-05 06:00:00+00:00  1756.751333      61880.0  33151.367357  
...                                ...          ...           ...  
2023-12-28 06:00:00+00:00     3.949965        154.0  42591.121852  
2023-12-29 06:00:00+00:00     7.872202        133.0  42595.568664  
2023-12-30 06:00:00+00:00     1.218782         93.0  41968.116472  
2023-12-31 06:00:00+00:00     1.065187         58.0  42523.345868  
2024-01-01 06:00:00+00:00     0.936692        131.0  43184.178175  

[1096 rows x 7 columns]

# strategy

In [70]:
df_btc = df_crypto.loc[('BTC/USD')]
df_btc

open       high         low      close  \
timestamp                                                                
2021-01-01 06:00:00+00:00  29255.710  29682.290  28707.5600  29676.790   
2021-01-02 06:00:00+00:00  29678.340  34200.000  29555.9900  33769.520   
2021-01-03 06:00:00+00:00  33769.520  34812.930  32300.6100  32908.020   
2021-01-04 06:00:00+00:00  32907.360  33496.030  27900.0000  30441.570   
2021-01-05 06:00:00+00:00  30461.840  35851.420  29927.5500  35063.000   
...                              ...        ...         ...        ...   
2023-12-28 06:00:00+00:00  43219.050  43219.050  42168.3170  42703.000   
2023-12-29 06:00:00+00:00  42677.465  43111.110  41552.0500  42077.970   
2023-12-30 06:00:00+00:00  42105.110  42585.069  41536.2170  42206.355   
2023-12-31 06:00:00+00:00  42177.102  42852.700  42103.7605  42225.540   
2024-01-01 06:00:00+00:00  42212.570  43857.800  42212.5700  43412.165   

                                volume  trade_count          vwap  
timestamp                                                          
2021-01-01 06:00:00+00:00   848.874030      29639.0  29316.444625  
2021-01-02 06:00:00+00:00  2144.592516      60152.0  31941.412694  
2021-01-03 06:00:00+00:00  1838.695433      58725.0  33505.269474  
2021-01-04 06:00:00+00:00  2711.189503      69226.0  31267.965121  
2021-01-05 06:00:00+00:00  1756.751333      61880.0  33151.367357  
...                                ...          ...           ...  
2023-12-28 06:00:00+00:00     3.949965        154.0  42591.121852  
2023-12-29 06:00:00+00:00     7.872202        133.0  42595.568664  
2023-12-30 06:00:00+00:00     1.218782         93.0  41968.116472  
2023-12-31 06:00:00+00:00     1.065187         58.0  42523.345868  
2024-01-01 06:00:00+00:00     0.936692        131.0  43184.178175  

[1096 rows x 7 columns]

In [71]:
df_btc.shape

(1096, 7)

In [72]:

# Load your data
# data = ...

# Calculate indicators
ma = vbt.MA.run(df_btc['close'], window=50)
macd = vbt.MACD.run(df_btc['close'])
atr = vbt.ATR.run(df_btc['high'], df_btc['low'], df_btc['close'])
obv = vbt.OBV.run(df_btc['close'], df_btc['volume'])
rsi = vbt.RSI.run(df_btc['close'])
stoch = vbt.STOCH.run(df_btc['high'], df_btc['low'], df_btc['close'])

# Define your signals
buy_signals = (
    (df_btc['close'] > ma.ma)# & # Price is above MA
    #(macd.macd > macd.signal) & # MACD line is above the signal line
    #(obv.obv > obv.obv.rolling(window=50).mean()) & # OBV is in uptrend
    #(rsi.rsi < 30) # RSI indicates oversold
)

sell_signals = (
    (df_btc['close'] < ma.ma) | # Price is below MA
    (rsi.rsi > 70) # RSI indicates overbought
)

# Use ATR for stop-loss distance, example: 2 * ATR
#stop_loss_price = df_btc['close'] - atr.tr * 2

buy_signals.value_counts(), sell_signals.value_counts(), buy_signals.shape, sell_signals.shape


(False    594
 True     502
 Name: count, dtype: int64,
 True     694
 False    402
 Name: count, dtype: int64,
 (1096,),
 (1096,))

## indicators plots

In [73]:
fig = ma.plot()
fig.show()

In [74]:
fig = macd.plot()
fig.show()

In [75]:
fig = atr.plot()
fig.show()

In [76]:
fig = obv.plot()
fig.show()

In [77]:
fig = rsi.plot()
fig.show()

In [78]:
fig = stoch.plot()
fig.show()

## overlay plots

In [79]:
ma50 = vbt.MA.run(df_btc['close'], window=50)
ma200 = vbt.MA.run(df_btc['close'], window = 200)

fig = df_btc['close'].vbt.plot()
fig = ma50.ma.vbt.plot(trace_kwargs=dict(name='Fast MA 50', line_color='orange'), 
                       fig = fig)
fig = ma200.ma.vbt.plot(trace_kwargs=dict(name='Slow MA 200', line_color='red'), 
                       fig = fig)
fig.show()

In [80]:
fig2 = buy_signals.vbt.signals.plot_as_entry_markers(df_btc['close'], fig=fig, trace_kwargs=dict(name='Entry', marker_color='blue', marker_size=10))
fig2 = sell_signals.vbt.signals.plot_as_exit_markers(df_btc['close'], fig=fig2, trace_kwargs=dict(name='Exit', marker_color='purple', marker_size=10))
fig2.show()

## plots in grid

In [81]:
fig = make_subplots(rows=2, cols=2, subplot_titles=('Volume', 'Price with MAs', 
                                                    'Price with entries', 'Price with exits'))

# chart 1 - volume

volume_trace = go.Scatter(x=df_btc.index, y=df_btc['volume'], mode='lines', name='Volume')
fig.add_trace(volume_trace, row=1, col=1)

# chart 2 - MAs

ma50_trace = go.Scatter(x=df_btc.index, y=ma50.ma, mode='lines', name='Fast MA - 50', line=dict(color='orange'))
ma200_trace = go.Scatter(x=df_btc.index, y=ma200.ma, mode='lines', name='Slow MA - 200', line=dict(color='red'))
price_trace = go.Scatter(x = df_btc.index, y = df_btc['close'], name= 'Close price', line = dict(color = 'blue'))

fig.add_trace(price_trace, row=1, col=2)
fig.add_trace(ma50_trace, row=1, col=2)
fig.add_trace(ma200_trace, row=1, col=2)

# chart 3 - price + entries

entry_trace = go.Scatter(x=buy_signals[buy_signals == True].index, y=df_btc.loc[buy_signals == True, 'close'], mode='markers', name='Entry', marker=dict(color='green', size=10))

fig.add_trace(entry_trace, row = 2, col = 1)
fig.add_trace(price_trace, row=2, col=1)

# chart 4 - price + exits

exit_trace = go.Scatter(x=sell_signals[sell_signals == True].index, y=df_btc.loc[sell_signals == True, 'close'], mode='markers', name='Entry', marker=dict(color='red', size=10))

fig.add_trace(exit_trace, row = 2, col = 2)
fig.add_trace(price_trace, row=2, col=2)

fig.update_layout(height=800, width=1200, title_text="Indicators and signals Plots", showlegend=True)

fig.write_html('..\\reports\\indicators_signals_gridplot.html')
fig.show()


## portfolio

In [82]:
# Backtest the strategy
portfolio = vbt.Portfolio.from_signals(
    df_btc['close'],
    buy_signals,
    #sell_signals,
    #sl_trail = True,
    sl_stop = 0.025,
    tp_stop = 0.05,
    size=1,  # assuming one unit per trade, can be adjusted
    fees=0.001,  # assuming 0.1% trading fees, can be adjusted
    freq='1D'  # assuming daily frequency, can be adjusted
)

# Analyze the performance
performance = portfolio.stats()
print(performance)

Start                         2021-01-01 06:00:00+00:00
End                           2024-01-01 06:00:00+00:00
Period                               1096 days 00:00:00
Start Value                                       100.0
End Value                                    137.608725
Total Return [%]                              37.608725
Benchmark Return [%]                          46.283223
Max Gross Exposure [%]                            100.0
Total Fees Paid                               17.523368
Max Drawdown [%]                              40.906148
Max Drawdown Duration                 540 days 00:00:00
Total Trades                                         92
Total Closed Trades                                  91
Total Open Trades                                     1
Open Trade PnL                                 3.688413
Win Rate [%]                                  46.153846
Best Trade [%]                                13.644865
Worst Trade [%]                              -12

### portfolio plots

In [83]:
fig = portfolio.plot()
fig.show()

### portfolio trades

In [84]:
portfolio.entry_trades.records_readable

Entry Trade Id  Column      Size           Entry Timestamp  \
0                0       0  0.001794 2021-02-19 06:00:00+00:00   
1                1       0  0.001781 2021-02-23 06:00:00+00:00   
2                2       0  0.001692 2021-02-26 06:00:00+00:00   
3                3       0  0.001636 2021-02-28 06:00:00+00:00   
4                4       0  0.001619 2021-03-02 06:00:00+00:00   
..             ...     ...       ...                       ...   
87              87       0  0.003188 2023-12-09 06:00:00+00:00   
88              88       0  0.003218 2023-12-11 06:00:00+00:00   
89              89       0  0.003251 2023-12-22 06:00:00+00:00   
90              90       0  0.003186 2023-12-27 06:00:00+00:00   
91              91       0  0.003170 2023-12-30 06:00:00+00:00   

    Avg Entry Price  Entry Fees            Exit Timestamp  Avg Exit Price  \
0        55683.6500    0.099900 2021-02-22 06:00:00+00:00      49950.0900   
1        50217.2500    0.089435 2021-02-25 06:00:00+00:00      45499.2900   
2        47791.2800    0.080870 2021-02-27 06:00:00+00:00      44803.8300   
3        46235.2500    0.075664 2021-03-01 06:00:00+00:00      48703.5500   
4        49132.9300    0.079544 2021-03-04 06:00:00+00:00      47143.6000   
..              ...         ...                       ...             ...   
87       43895.5735    0.139924 2023-12-10 06:00:00+00:00      42027.1580   
88       41547.5450    0.133700 2023-12-21 06:00:00+00:00      44164.6955   
89       43626.7550    0.141838 2023-12-26 06:00:00+00:00      42451.7150   
90       43235.6150    0.137742 2023-12-29 06:00:00+00:00      42077.9700   
91       42206.3550    0.133787 2024-01-01 06:00:00+00:00      43412.1650   

    Exit Fees        PnL    Return Direction  Status  Position Id  
0    0.089614 -10.475894 -0.104864      Long  Closed            0  
1    0.081032  -8.572942 -0.095857      Long  Closed            1  
2    0.075815  -5.211916 -0.064448      Long  Closed            2  
3    0.079703   3.883985  0.051332      Long  Closed            3  
4    0.076323  -3.376490 -0.042448      Long  Closed            4  
..        ...        ...       ...       ...     ...          ...  
87   0.133968  -6.229757 -0.044522      Long  Closed           87  
88   0.142122   8.146194  0.060929      Long  Closed           88  
89   0.138018  -4.100125 -0.028907      Long  Closed           89  
90   0.134054  -3.959887 -0.028748      Long  Closed           90  
91   0.000000   3.688413  0.027569      Long    Open           91  

[92 rows x 14 columns]

In [85]:
buy_sell_signals = pd.DataFrame({'buy_signal': buy_signals,
                                 'sell_signal': sell_signals,
                                 'close_price':df_btc['close'],
                                 'ma':ma.ma})
buy_sell_signals

buy_signal  sell_signal  close_price           ma
timestamp                                                                   
2021-01-01 06:00:00+00:00       False        False    29676.790          NaN
2021-01-02 06:00:00+00:00       False        False    33769.520          NaN
2021-01-03 06:00:00+00:00       False        False    32908.020          NaN
2021-01-04 06:00:00+00:00       False        False    30441.570          NaN
2021-01-05 06:00:00+00:00       False        False    35063.000          NaN
...                               ...          ...          ...          ...
2023-12-28 06:00:00+00:00        True        False    42703.000  40147.74280
2023-12-29 06:00:00+00:00        True        False    42077.970  40253.94190
2023-12-30 06:00:00+00:00        True        False    42206.355  40355.94011
2023-12-31 06:00:00+00:00        True        False    42225.540  40458.51208
2024-01-01 06:00:00+00:00        True        False    43412.165  40587.80082

[1096 rows x 4 columns]

In [86]:
fig = portfolio.trades.plot()
fig.show()

# dummy strategy to check how the signals + trades work

In [87]:
df_btc_small = df_btc.iloc[:100]
df_btc_small.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 100 entries, 2021-01-01 06:00:00+00:00 to 2021-04-10 05:00:00+00:00
Data columns (total 7 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   open         100 non-null    float64
 1   high         100 non-null    float64
 2   low          100 non-null    float64
 3   close        100 non-null    float64
 4   volume       100 non-null    float64
 5   trade_count  100 non-null    float64
 6   vwap         100 non-null    float64
dtypes: float64(7)
memory usage: 6.2 KB


In [88]:
df_btc_small.head()

open      high       low     close  \
timestamp                                                           
2021-01-01 06:00:00+00:00  29255.71  29682.29  28707.56  29676.79   
2021-01-02 06:00:00+00:00  29678.34  34200.00  29555.99  33769.52   
2021-01-03 06:00:00+00:00  33769.52  34812.93  32300.61  32908.02   
2021-01-04 06:00:00+00:00  32907.36  33496.03  27900.00  30441.57   
2021-01-05 06:00:00+00:00  30461.84  35851.42  29927.55  35063.00   

                                volume  trade_count          vwap  
timestamp                                                          
2021-01-01 06:00:00+00:00   848.874030      29639.0  29316.444625  
2021-01-02 06:00:00+00:00  2144.592516      60152.0  31941.412694  
2021-01-03 06:00:00+00:00  1838.695433      58725.0  33505.269474  
2021-01-04 06:00:00+00:00  2711.189503      69226.0  31267.965121  
2021-01-05 06:00:00+00:00  1756.751333      61880.0  33151.367357

In [89]:
fig = df_btc_small.close.vbt.plot()
fig.show()

In [90]:
# long signals

entry_long_signals_small = pd.Series(np.repeat(False, len(df_btc_small)), index = df_btc_small.index)
entry_long_signals_small.loc['2021-01-26'] = True
entry_long_signals_small.loc['2021-02-27'] = True
entry_long_signals_small.loc['2021-03-24'] = True

exit_long_signals_small = pd.Series(np.repeat(False, len(df_btc_small)), index = df_btc_small.index)
exit_long_signals_small.loc['2021-02-20'] = True
exit_long_signals_small.loc['2021-03-13'] = True
exit_long_signals_small.loc['2021-04-01'] = True

# short signals

entry_short_signals_small = pd.Series(np.repeat(False, len(df_btc_small)), index = df_btc_small.index)
entry_short_signals_small.loc['2021-01-09'] = True
entry_short_signals_small.loc['2021-02-21'] = True
entry_short_signals_small.loc['2021-03-17'] = True

exit_short_signals_small = pd.Series(np.repeat(False, len(df_btc_small)), index = df_btc_small.index)
exit_short_signals_small.loc['2021-01-24'] = True
exit_short_signals_small.loc['2021-02-26'] = True
exit_short_signals_small.loc['2021-03-23'] = True

In [91]:
entry_long_signals_small.value_counts()

False    97
True      3
Name: count, dtype: int64

In [92]:
portfolio = vbt.Portfolio.from_signals(
    df_btc_small['close'], # reference price - what does it mean?
    entry_long_signals_small,
    exit_long_signals_small,
    entry_short_signals_small,
    exit_short_signals_small,
    #price = df_btc_small['open'], # execution price?
    #sl_trail = True,
    sl_stop = 0.025,
    tp_stop = 0.05,
    size=200,  # order size, can be as vector
    size_type = 'value',
    slippage = 0.001,
    fees=0.001,  # assuming 0.1% trading fees, can be adjusted
    #init_cash = 10_000,
    freq='1D'  # assuming daily frequency, can be adjusted
)

In [93]:
fig = portfolio.plot()
fig.show()

In [94]:
portfolio.stats()

Start                         2021-01-01 06:00:00+00:00
End                           2021-04-10 05:00:00+00:00
Period                                100 days 00:00:00
Start Value                                       100.0
End Value                                    192.091399
Total Return [%]                              92.091399
Benchmark Return [%]                         101.735262
Max Gross Exposure [%]                            100.0
Total Fees Paid                                2.097178
Max Drawdown [%]                               1.298262
Max Drawdown Duration                   1 days 00:00:00
Total Trades                                          6
Total Closed Trades                                   6
Total Open Trades                                     0
Open Trade PnL                                      0.0
Win Rate [%]                                      100.0
Best Trade [%]                                13.752617
Worst Trade [%]                                4

In [95]:
fig = portfolio.trades.plot()
fig.show()

In [96]:
portfolio.trades.records_readable

Exit Trade Id  Column      Size           Entry Timestamp  Avg Entry Price  \
0              0       0  0.004932 2021-01-09 06:00:00+00:00      40506.87258   
1              1       0  0.004033 2021-01-26 06:00:00+00:00      31579.59805   
2              2       0  0.003580 2021-02-21 06:00:00+00:00      55809.65448   
3              3       0  0.003467 2021-02-27 06:00:00+00:00      44848.63383   
4              4       0  0.003400 2021-03-17 05:00:00+00:00      58756.10508   
5              5       0  0.003495 2021-03-24 05:00:00+00:00      52305.37312   

   Entry Fees            Exit Timestamp  Avg Exit Price  Exit Fees        PnL  \
0    0.199800 2021-01-10 06:00:00+00:00        34860.75   0.171951  27.477728   
1    0.127350 2021-01-29 06:00:00+00:00        33517.18   0.135164   7.551131   
2    0.199800 2021-02-22 06:00:00+00:00        49950.09   0.178823  20.598769   
3    0.155472 2021-03-01 06:00:00+00:00        48703.55   0.168836  13.039135   
4    0.199800 2021-03-22 05:00:00+00:00        54424.88   0.185072  14.343449   
5    0.182827 2021-03-26 05:00:00+00:00        55010.74   0.192284   9.081186   

     Return Direction  Status  Position Id  
0  0.137526     Short  Closed            0  
1  0.059294      Long  Closed            1  
2  0.103097     Short  Closed            2  
3  0.083868      Long  Closed            3  
4  0.071789     Short  Closed            4  
5  0.049671      Long  Closed            5

# higher highs/lows strategy

In [129]:
df_btc = btc_data_yf
#df_btc = df_crypto.loc[('BTC/USD')]
df_btc.columns = [col.lower() for col in df_btc.columns]
#df_btc = df_btc['2021-01-01':]
df_btc.head()

open        high         low       close   adj close  \
Date                                                                     
2014-09-17  465.864014  468.174011  452.421997  457.334015  457.334015   
2014-09-18  456.859985  456.859985  413.104004  424.440002  424.440002   
2014-09-19  424.102997  427.834991  384.532013  394.795990  394.795990   
2014-09-20  394.673004  423.295990  389.882996  408.903992  408.903992   
2014-09-21  408.084991  412.425995  393.181000  398.821014  398.821014   

              volume  
Date                  
2014-09-17  21056800  
2014-09-18  34483200  
2014-09-19  37919700  
2014-09-20  36863600  
2014-09-21  26580100

In [130]:
# parameters
#   entry
window_entry_identify = 5  # rolling window for identification of higher highs and higher lows
window_entry_count = 5  # Rolling window for calculation of count of higher highs and higher lows for entry signal
hh_hl_counts = 3   # Minimum number of higher highs and higher lows required for entry

#   exit
window_exit_identify = 5 # rolling window for identification of lower highs for exit signal
window_exit_count = 5 # rolling window to calculate counts of lower highs
lh_counts = 1 # number of lower highs to trigger an exit signal


# Identify higher highs and higher lows

higher_highs = df_btc['close'] > df_btc['close'].rolling(window_entry_identify, min_periods=1).max().shift(1)
higher_lows = df_btc['close'] > df_btc['close'].rolling(window_entry_identify, min_periods=1).min().shift(1)

# Count occurrences over the rolling window

hh_count = higher_highs.rolling(window_entry_count).sum()
hl_count = higher_lows.rolling(window_entry_count).sum()

# Entry signal: Next higher low after at least M higher highs and higher lows

entry_signal = (hl_count.shift(1) >= hh_hl_counts) & (hh_count.shift(1) >= hh_hl_counts) & higher_lows

# Exit signal: lower high occurrence

lower_highs = df_btc['close'] < df_btc['close'].rolling(window_exit_identify, min_periods=1).max().shift(1)
lh_count = lower_highs.rolling(window_exit_count).sum()
exit_signal = (lh_count >= lh_counts) & lower_highs

# Create and backtest the portfolio

portfolio = vbt.Portfolio.from_signals(df_btc['close'], 
                                       entry_signal, 
                                       exit_signal,
                                       price = df_btc['open'].shift(-1), # execution price is next day open
                                       fees = 0.001,
                                       slippage = 0.0001,
                                       freq = '1D')

# Print the performance
print(portfolio.stats())


Start                               2014-09-17 00:00:00
End                                 2023-12-31 00:00:00
Period                               3393 days 00:00:00
Start Value                                       100.0
End Value                                   2127.161758
Total Return [%]                            2027.161758
Benchmark Return [%]                        9141.645302
Max Gross Exposure [%]                            100.0
Total Fees Paid                               155.34675
Max Drawdown [%]                              39.025403
Max Drawdown Duration                 884 days 00:00:00
Total Trades                                         88
Total Closed Trades                                  88
Total Open Trades                                     0
Open Trade PnL                                      0.0
Win Rate [%]                                  44.318182
Best Trade [%]                               105.847303
Worst Trade [%]                              -22

In [131]:
fig = portfolio.trades.plot()
fig.show()

In [132]:
fig = portfolio.plot()
fig.show()

In [133]:
df_check = pd.DataFrame({'close':df_btc['close'],
                         'next_day_open':df_btc['open'].shift(-1),
                         'higher_highs':higher_highs,
                         'higher_lows':higher_lows,
                         'hh_count':hh_count,
                         'hl_count':hl_count,
                         'entry_signal':entry_signal,
                         'lower_highs':lower_highs,
                         'lh_count':lh_count,
                         'exit_signal':exit_signal})
df_check

close  next_day_open  higher_highs  higher_lows  hh_count  \
Date                                                                           
2014-09-17    457.334015     456.859985         False        False       NaN   
2014-09-18    424.440002     424.102997         False        False       NaN   
2014-09-19    394.795990     394.673004         False        False       NaN   
2014-09-20    408.903992     408.084991         False         True       NaN   
2014-09-21    398.821014     399.100006         False         True       0.0   
...                  ...            ...           ...          ...       ...   
2023-12-27  43442.855469   43468.199219         False         True       0.0   
2023-12-28  42627.855469   42614.644531         False         True       0.0   
2023-12-29  42099.402344   42091.753906         False        False       0.0   
2023-12-30  42156.902344   42152.097656         False         True       0.0   
2023-12-31  42265.187500            NaN         False         True       0.0   

            hl_count  entry_signal  lower_highs  lh_count  exit_signal  
Date                                                                    
2014-09-17       NaN         False        False       NaN        False  
2014-09-18       NaN         False         True       NaN        False  
2014-09-19       NaN         False         True       NaN        False  
2014-09-20       NaN         False         True       NaN        False  
2014-09-21       2.0         False         True       4.0         True  
...              ...           ...          ...       ...          ...  
2023-12-27       4.0         False         True       5.0         True  
2023-12-28       4.0         False         True       5.0         True  
2023-12-29       3.0         False         True       5.0         True  
2023-12-30       3.0         False         True       5.0         True  
2023-12-31       4.0         False         True       5.0         True  

[3393 rows x 10 columns]

In [134]:
df_trades = portfolio.trades.records_readable
df_trades

Exit Trade Id  Column      Size Entry Timestamp  Avg Entry Price  \
0               0       0  0.249130      2014-10-14       400.995082   
1               1       0  0.265839      2014-11-10       365.893580   
2               2       0  0.416457      2015-01-24       247.376740   
3               3       0  0.351674      2015-03-02       275.073495   
4               4       0  0.421889      2015-06-12       229.942990   
..            ...     ...       ...             ...              ...   
83             83       0  0.056255      2023-06-20     28314.141678   
84             84       0  0.063501      2023-09-18     26763.527648   
85             85       0  0.056257      2023-10-21     29921.646162   
86             86       0  0.051906      2023-11-10     37313.801320   
87             87       0  0.048628      2023-11-29     37864.903299   

    Entry Fees Exit Timestamp  Avg Exit Price  Exit Fees         PnL  \
0     0.099900     2014-10-18      391.214872   0.097464   -2.633912   
1     0.097269     2014-11-16      388.310164   0.103228    5.758708   
2     0.103022     2015-01-29      232.748726   0.096930   -6.291890   
3     0.096736     2015-03-07      276.405371   0.097205    0.274445   
4     0.097010     2015-06-20      245.075496   0.103395    6.183828   
..         ...            ...             ...        ...         ...   
83    1.592813     2023-06-26    30271.292880   1.702912  106.803865   
84    1.699510     2023-09-21    26561.400235   1.686675  -16.221471   
85    1.683305     2023-10-30    34496.628117   1.940680  253.751174   
86    1.936802     2023-11-14    35544.558470   1.844968  -95.615718   
87    1.841282     2023-12-10    43787.640329   2.129291  284.038346   

      Return Direction  Status  Position Id  
0  -0.026365      Long  Closed            0  
1   0.059204      Long  Closed            1  
2  -0.061073      Long  Closed            2  
3   0.002837      Long  Closed            3  
4   0.063744      Long  Closed            4  
..       ...       ...     ...          ...  
83  0.067054      Long  Closed           83  
84 -0.009545      Long  Closed           84  
85  0.150746      Long  Closed           85  
86 -0.049368      Long  Closed           86  
87  0.154261      Long  Closed           87  

[88 rows x 14 columns]

# TODOS

In [ ]:
# MA crossover strategy

#   podmienky EXIT:
#      ked cena crossne MA
#      alebo ked v MA nastane reversal a zacne zrychlovat
#   podmienky ENTRY:
#      nejaku periodu bol MA v raste
#      nejaku dobu potom bol MA viac menej flat
#      cena ho viac krat crossla ked bol flat?
#      potom MA zacal klesat a tento pokles sa zryhluje
#      rozdiel medzi cenou a MA sa zvacsuje
#      ak v teraz nastal cross, kup/predaj

# strategy 2

#   ak cena robi N dni po sebe lower lows / higher highs via ako P percent, ENTRY
#      na celej BTC periode walk-forward optimalizacia (range split vs. rolling split) + evaluacia
#      zbehnut to na vsetkych kryptomenach a vsetkych equities
#      vylepsit strategiu nejakym MA (odfiltrovanie zlych entries), stop loss, ...
#      higher highs/lows ako min percento

# strategy 3

#   ak cena posledny P percent dni za poslednych N dni rastie

# strategy 4

#  ak je open price vyrazne ina ako predosly den close, kup/predaj, a na konci dna zavri
#  mozno len niektore dni, ako napr po vikende

# strategy 5

#   supporta a resistance identifikacia a nakup/predaj pri ich breaknuti

# strategy 6

#   ak cena prvu hodinu po otvoreni vyrazne vzrastie kup, predaj na konci dna

# strategy 7

# data od fin. analytikov - predikcia short term buy - voting viacerych zdrojov